In [2]:
import sys
sys.path.append("../src/")
sys.path.append("../")



import torch
from bert import *
from feature_data import *
from multiprototype import *
from models import *
from utils import *
from nltk.corpus import wordnet as wn
from nltk.corpus.reader.wordnet import Lemma
from scipy.stats import pearsonr
from scipy.stats import spearmanr
import matplotlib.pyplot as plt

import pandas as pd

pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
pd.set_option('display.width', None)
pd.set_option('display.colheader_justify', 'center')
pd.set_option('display.precision', 3)

In [3]:
bert = BERTBase()

INFO:pytorch_pretrained_bert.modeling:loading archive file https://s3.amazonaws.com/models.huggingface.co/bert/bert-base-uncased.tar.gz from cache at /Users/gabriellachronis/.pytorch_pretrained_bert/9c41111e2de84547a463fd39217199738d1e3deb72d4fec4399e6e241983c6f0.ae3cef932725ca7a30cdcb93fc6e09150a55e2a130ec7af63975a16c153ae2ba
INFO:pytorch_pretrained_bert.modeling:extracting archive file /Users/gabriellachronis/.pytorch_pretrained_bert/9c41111e2de84547a463fd39217199738d1e3deb72d4fec4399e6e241983c6f0.ae3cef932725ca7a30cdcb93fc6e09150a55e2a130ec7af63975a16c153ae2ba to temp dir /var/folders/9m/vzvx58rs51v_x5nm620fz4xr0000gn/T/tmphe4i2x3r
INFO:pytorch_pretrained_bert.modeling:Model config {
  "attention_probs_dropout_prob": 0.1,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "max_position_embeddings": 512,
  "num_attention_heads": 12,
  "num_hidden_layers": 12,
  "type_vocab_size": 2,
  "vocab_size": 3

In [39]:
"""
take a look at the eval words
"""

"""
parse into a dataset with id, orig_sent, and swap_sent
"""

pd.set_option('display.max_colwidth', None)


try:
   from itertools import izip_longest
except ImportError:  # Python 3
    from itertools import zip_longest as izip_longest

def grouper(iterable, n, fillvalue=None):
    args = [iter(iterable)] * n
    return izip_longest(*args, fillvalue=fillvalue)

filename = '../data/external/swapped_treebank_sents.txt'

items = []
with open(filename) as f:
     for lines in grouper(f, 3, ''):
        assert len(lines) == 3
        sent = lines[1]
        swapped_sent = lines[2]

        orig_split = sent.split(' ')
        swap_split = swapped_sent.split(' ')

        i = 0
        try:
            while orig_split[i] == swap_split[i]:
                i +=1


            original_subject = orig_split[i]
            original_object = swap_split[i]
        
            item = {"id": lines[0],
                    "sent": lines[1],
                    "subject": original_subject,
                    "object": original_object,
                    "swapped?": False}
            items.append(item)       

            item = {"id": lines[0],
                    "sent": lines[2],
                    "subject": original_object,
                    "object": original_subject,
                    "swapped?": True}
            items.append(item)       

        except:
            continue
        
        



    
df = pd.DataFrame(items)


df

id                                                      \
0                                                                                         reviews-211797-0020\n   
1                                                                                         reviews-211797-0020\n   
2                                                                                         reviews-211797-0007\n   
3                                                                                         reviews-211797-0007\n   
4                                                                                         reviews-053248-0002\n   
5                                                                                         reviews-053248-0002\n   
6                                                                                         reviews-363685-0030\n   
7                                                                                         reviews-363685-0030\n   
8                                                                                         reviews-363685-0010\n   
9                                                                                         reviews-363685-0010\n   
10                                                                                        reviews-290594-0006\n   
11                                                                                        reviews-290594-0006\n   
12                                                                                        reviews-290594-0005\n   
13                                                                                        reviews-290594-0005\n   
14                                                                                        reviews-026883-0010\n   
15                                                                                        reviews-026883-0010\n   
16                                                                                        reviews-036133-0009\n   
17                                                                                        reviews-036133-0009\n   
18                                                                                        reviews-018465-0012\n   
19                                                                                        reviews-018465-0012\n   
20                                                                                        reviews-018465-0011\n   
21                                                                                        reviews-018465-0011\n   
22                                                                                        reviews-220214-0004\n   
23                                                                                        reviews-220214-0004\n   
24                                                                                        reviews-269560-0009\n   
25                                                                                        reviews-269560-0009\n   
26                                                                                        reviews-018548-0014\n   
27                                                                                        reviews-018548-0014\n   
28                                                                                        reviews-216456-0004\n   
29                                                                                        reviews-216456-0004\n   
30                                                                                        reviews-326649-0007\n   
31                                                                                        reviews-326649-0007\n   
32                                                                                        reviews-210066-0006\n   
33                                                                                        reviews-210066-0006\n   
34                              

In [33]:
"""
ok you want to see analyses and comepare these 4

naturaal subjecs
natural objects

subjects swapped to objects
objects swapped to subjects

"""

In [41]:
len(df)

966

In [18]:
long_form = [
    'Features [Vision - Vision]',
'Features [Vision - Bright]',
'Features [Vision - Dark]',
'Features [Vision - Color]',
'Features [Vision - Pattern]',
'Features [Vision - Large]',
'Features [Vision - Small]',
'Features [Vision - Motion]',
'Features [Vision - Biomotion]',
'Features [Vision - Fast]',
'Features [Vision - Slow]',
'Features [Vision - Shape]',
'Features [Vision - Face]',
'Features [Vision - Body]',
'Features [Somatic - Touch]',
'Features [Somatic - Temperature]',
'Features [Somatic - Texture]',
'Features [Somatic - Weight]',
'Features [Somatic - Pain]',
'Features [Audition - Audition]',
'Features [Audition - Loud]',
'Features [Audition - Low]',
'Features [Audition - High]',
'Features [Audition - Sound]',
'Features [Audition - Music]',
'Features [Audition - Speech]',
'Features [Gustation - Taste]',
'Features [Olfaction - Smell]',
'Features [Motor - Head]',
'Features [Motor - UpperLimb]',
'Features [Motor - LowerLimb]',
'Features [Spatial - Landmark]',
'Features [Spatial - Path]',
'Features [Spatial - Scene]',
'Features [Spatial - Near]',
'Features [Spatial - Toward]',
'Features [Spatial - Away]',
'Features [Spatial - Number]',
'Features [Temporal - Time]',
'Features [Temporal - Duration]',
'Features [Temporal - Long]',
'Features [Temporal - Short]',
'Features [Causal - Consequential]',
'Features [Social - Social]',
'Features [Social - Human]',
'Features [Social - Communication]',
'Features [Social - Self]',
'Features [Cognition - Cognition]',
'Features [Emotion - Benefit]',
'Features [Emotion - Harm]',
'Features [Emotion - Pleasant]',
'Features [Emotion - Unpleasant]',
'Features [Emotion - Happy]',
'Features [Emotion - Sad]',
'Features [Emotion - Angry]',
'Features [Emotion - Disgusted]',
'Features [Emotion - Fearful]',
'Features [Emotion - Surprised]',
'Features [Drive - Drive]',
'Features [Drive - Needs]',
'Features [Attention - Attention]',
'Features [Attention - Arousal]'
]

feature_categories = dict()

for col in long_form:
    feature = col.split()[-1][:-1]
    category = col.split()[1][1:]
    feature_categories[feature] = category

features = feature_categories.keys()

feature_categories

{'Vision': 'Vision',
 'Bright': 'Vision',
 'Dark': 'Vision',
 'Color': 'Vision',
 'Pattern': 'Vision',
 'Large': 'Vision',
 'Small': 'Vision',
 'Motion': 'Vision',
 'Biomotion': 'Vision',
 'Fast': 'Vision',
 'Slow': 'Vision',
 'Shape': 'Vision',
 'Face': 'Vision',
 'Body': 'Vision',
 'Touch': 'Somatic',
 'Temperature': 'Somatic',
 'Texture': 'Somatic',
 'Weight': 'Somatic',
 'Pain': 'Somatic',
 'Audition': 'Audition',
 'Loud': 'Audition',
 'Low': 'Audition',
 'High': 'Audition',
 'Sound': 'Audition',
 'Music': 'Audition',
 'Speech': 'Audition',
 'Taste': 'Gustation',
 'Smell': 'Olfaction',
 'Head': 'Motor',
 'UpperLimb': 'Motor',
 'LowerLimb': 'Motor',
 'Landmark': 'Spatial',
 'Path': 'Spatial',
 'Scene': 'Spatial',
 'Near': 'Spatial',
 'Toward': 'Spatial',
 'Away': 'Spatial',
 'Number': 'Spatial',
 'Time': 'Temporal',
 'Duration': 'Temporal',
 'Long': 'Temporal',
 'Short': 'Temporal',
 'Consequential': 'Causal',
 'Social': 'Social',
 'Human': 'Social',
 'Communication': 'Social',
 'Se

In [42]:
# model dimensions dont have full 65 oops who knows what happened if our original downloaded data was bunk
len(feature_categories)

62

In [43]:
model = torch.load('../trained_models/model.ffnn.binder.1k.50epochs.0.5dropout.lr1e-4.hsize300')

In [59]:
subject_predictions = []
object_predictions = []
for index, row in df.iterrows():
        
    # predict features in context
#     singular = row.word
#     past = singular+"d"
#     try:
#         prediction = model.predict_in_context(singular, row.sentence, bert)
#         word = singular
#     except:
#         prediction = model.predict_in_context(past, row.sentence, bert)
#         word = past

    print(row.subject)
    print(row.sent)
    subject_prediction = model.predict_in_context(row.subject, row.sent, bert)
    subject_predictions.append(subject_prediction)
    
    object_prediction = model.predict_in_context(row.object, row.sent, bert)
    object_predictions.append(object_prediction)
    
    
df['subject_predictions'] = subject_predictions
df['object_predictions'] = object_predictions

shops
Other shops around this city have MUCH NICER and more TRANSPARENT owners .

owners
Other owners around this city have MUCH NICER and more TRANSPARENT shops .

person
Hmmm ... A person can not call a company , if you have no idea its name ( since the designer is unknown ... SUPPOSEDLY ) , and order a gown without a dress name or style number .

company
Hmmm ... A company can not call a person , if you have no idea its name ( since the designer is unknown ... SUPPOSEDLY ) , and order a gown without a dress name or style number .

people
The worst thing that can happen for any restaurant like Zahav is to have too many people write hyperbolic reviews making claims that " everyone " is going to " love " the food , decor and service .

reviews
The worst thing that can happen for any restaurant like Zahav is to have too many reviews write hyperbolic people making claims that " everyone " is going to " love " the food , decor and service .

Inn
The Inn touts a shower with dual shower hea

menu
The menu had plenty of options even for picky eaters .

plenty
The plenty had menu of options even for picky eaters .

Johnette
I googled Garage Door Repair in Woodinville and found NDI - Johnette answered the phone and was oh - so pleasant and helpful !

phone
I googled Garage Door Repair in Woodinville and found NDI - phone answered the Johnette and was oh - so pleasant and helpful !

Kelly
Kelly hit the nail on the head .

nail
nail hit the Kelly on the head .

decor
The decor left a lot to be desired and the posters telling me all the reasons 99 was great just served as an ironic contrast against the reality .

lot
The lot left a decor to be desired and the posters telling me all the reasons 99 was great just served as an ironic contrast against the reality .

finger
The food was finger licking the bowel fantastic ..

bowel
The food was bowel licking the finger fantastic ..

doctor
I sincerely wonder if the doctor has a clue about what is going on within his practice .

clue
I

Other
Other will add a drop of Methylene blue .

drop
drop will add a Other of Methylene blue .

Ireland
Ireland receives a lot of rain , with certain areas getting a soaking as many as 270 days of the year .

lot
lot receives a Ireland of rain , with certain areas getting a soaking as many as 270 days of the year .

bulb
The long tube UVB bulbs are best , like Zoomed 's Repsitun model : http://lllreptile.com/store/catalog/reptile-supplies/uvb-fluorescent-lights-mercury-vapor-bulbs/-/zoo-med-24-repti-sun-100-fluorescent-bulb/ Remember to replace UVB bulbs according to the manufacturer s recommendation after which time the bulb will no longer produce UVB even if visible light still is .

UVB
The long tube UVB bulbs are best , like Zoomed 's Repsitun model : http://lllreptile.com/store/catalog/reptile-supplies/uvb-fluorescent-lights-mercury-vapor-bulbs/-/zoo-med-24-repti-sun-100-fluorescent-bulb/ Remember to replace UVB bulbs according to the manufacturer s recommendation after which tim

cat
Given the chance your cat may only have one kidney , I would think the worst case scenario would be kidney disease , which untreated can lead to possible renal failure .

kidney
Given the chance your kidney may only have one cat , I would think the worst case scenario would be kidney disease , which untreated can lead to possible renal failure .

cat
But your cat is passing a LOT of urine , and this is bad .

LOT
But your LOT is passing a cat of urine , and this is bad .

vet
When she was spayed the vet had a hard time because she only has one uterine horn and he said this could mean she only has on kidney .

time
When she was spayed the time had a hard vet because she only has one uterine horn and he said this could mean she only has on kidney .

Parisians
Parisians dislike Americans for their lack of speaking French and proper French manners .

Americans
Americans dislike Parisians for their lack of speaking French and proper French manners .

towns
Both towns have airports that 

Economist
17 - On 17 November 2001 , The Economist printed a correction for having said George Bush was properly elected in 2000 .

correction
17 - On 17 November 2001 , The correction printed a Economist for having said George Bush was properly elected in 2000 .

Bush
49 - Percentage of Americans who approved of the way Bush was handling his job as president in May 2004 .

job
49 - Percentage of Americans who approved of the way job was handling his Bush as president in May 2004 .

Bush
50 - Percentage of Americans who approved of the way Bush was handling his job as president on 15 October 2003 .

job
50 - Percentage of Americans who approved of the way job was handling his Bush as president on 15 October 2003 .

Bush
54 - Percentage of Americans who approved of the way Bush was handling his job as president on 30 September , 2003 .

job
54 - Percentage of Americans who approved of the way job was handling his Bush as president on 30 September , 2003 .

Bush
67 - Percentage of Americ

...

issues
The issues of the last few years have amplified four events , which have always existed , but have never been as rampant as in the present upheaval in the region .

Egypt
Egypt did not use poison gas against Yemen in the 60's because of Israel .

gas
gas did not use poison Egypt against Yemen in the 60's because of Israel .

kg
5 kg per gun , 200,000 guns means 1000 tonnes , impossible for 4 containers .

tonnes
5 tonnes per gun , 200,000 guns means 1000 kg , impossible for 4 containers .

reappropriation
Does this reappropriation lead to or originate from the same place ?

place
Does this place lead to or originate from the same reappropriation ?

Chiara
It emerged that Chiara , the girl who disappeared with Fabio , had a collection of satanic literature and paraphernalia in her bedroom .

collection
It emerged that collection , the girl who disappeared with Fabio , had a Chiara of satanic literature and paraphernalia in her bedroom .

author
Since the article was specifically 

Pakistan
Their removal should also provide increased motivation for Pakistan to help the return of moderate Taliban .

return
Their removal should also provide increased motivation for return to help the Pakistan of moderate Taliban .

Pakistan
Until now Pakistan has not facilitated such a return and clearly it can not happen until there is both a pull from Kabul and a push from Islamabad .

return
Until now return has not facilitated such a Pakistan and clearly it can not happen until there is both a pull from Kabul and a push from Islamabad .

US
Musharraf has always maintained that the US has never provided actionable intelligence about Taliban leaders hiding in Baluchistan .

intelligence
Musharraf has always maintained that the intelligence has never provided actionable US about Taliban leaders hiding in Baluchistan .

army
Not only is the army facing serious political fallout , growing anti-Americanism and anti-army feeling in the tribal areas but it is also taking heavy casualti

Sha'lan
Chalabi describing Sha'lan as a " Ba'athist " and a " former double agent for Saddam and the CIA " , while Sha'lan dismisses Chalabi as a " thief " and an " Iranian stooge who longs for his own origins by defending Iran " .

Chalabi
Chalabi describing Sha'lan as a " Ba'athist " and a " former double agent for Saddam and the CIA " , while Chalabi dismisses Sha'lan as a " thief " and an " Iranian stooge who longs for his own origins by defending Iran " .

Kerry
And it should be noted in passing that Kerry has personally questioned Bush ’s service , while Bush has not personally questioned Kerry ’s .

service
And it should be noted in passing that service has personally questioned Bush ’s Kerry , while Bush has not personally questioned Kerry ’s .

Bush
And it should be noted in passing that Kerry has personally questioned Bush ’s service , while Bush has not personally questioned Kerry ’s .

Kerry
And it should be noted in passing that Kerry has personally questioned Bush ’s serv

annexation
Ariel Sharon 's aggressive near annexation of almost half of the occupied West Bank and his indefinite postponement of any Palestinian state have created unprecedented rage and violence .

rage
Ariel Sharon 's aggressive near rage of almost half of the occupied West Bank and his indefinite postponement of any Palestinian state have created unprecedented annexation and violence .

assassination
Worse for Israel , the assassination drew a denunciation even from the moderate and cautious Grand Ayatollah Ali Sistani , who wields enormous moral authority over Iraqi Shiites .

denunciation
Worse for Israel , the denunciation drew a assassination even from the moderate and cautious Grand Ayatollah Ali Sistani , who wields enormous moral authority over Iraqi Shiites .

bungling
The bungling of post-war Iraq by the Bush administration created a weak and failed state .

state
The state of post-war Iraq by the Bush administration created a weak and failed bungling .

Iraq
If it is hard

observers
( This is a largely Sunni Arab clan , and some Sunni observers have accused Shiite elements in the government of being behind the assassination ; it is more likely the work of Sunni Arab guerrillas punishing the Batawi leaders for cooperating with the Dec. 15 elections . )

elements
( This is a largely Sunni Arab clan , and some Sunni elements have accused Shiite observers in the government of being behind the assassination ; it is more likely the work of Sunni Arab guerrillas punishing the Batawi leaders for cooperating with the Dec. 15 elections . )

killing
[ This killing of a respected cleric will be causing us trouble for years to come . ]

trouble
[ This trouble of a respected cleric will be causing us killing for years to come . ]



### This is the static analysis

when we see feature values for subjects, objects, and then swapped subjects, and swapped objects.

Should have a results table 65 X 4

For example, here is a sentence

Other shops around this city have MUCH NICER and more TRANSPARENT owners .\n

subject: shops
object: owners

And here is a swapped sentence

Other owners around this city have MUCH NICER and more TRANSPARENT shops .\n

subject: owners
object: shops

You can look at these four values separately, and that is what I will do. 


In [61]:
df.head(1)

id            \
0  reviews-211797-0020\n   

                                       sent                                      \
0  Other shops around this city have MUCH NICER and more TRANSPARENT owners .\n   

  subject  object  swapped?  \
0   shops  owners    False    

                                                                                                                                                                                                                                                                                                                                                                       predictions                                                                                                                                                                                                                                                                                                                                                                       \
0  [4.3799605, 1.2472309, 0.59806883, 0.9923664, 0.99339515, 2.2244937, 0.74286425, 0.094959944, -0.9846684, -0.20609444, -0.07528155, 1.8362715, -0.6636215, -0.71567607, 1.2664436, 0.26790407, 1.2734845, 2.3071332, -0.34670073, -0.1275428, -0.512184, -0.34024775, -0.28231272, 0.31037122, -0.7364459, -0.38705784, 0.2520091, 1.4410205, 0.29374498, 0.7736282, 0.7041685, 3.7295218, 0.32358542, 3.8077881, 3.0731666, 0.18642747, 0.41756785, 0.5527588, 0.20870416, 0.059482135, 0.13233602, 0.5092442, 0.4813312, 2.2625208, -0.20975313, 1.5789889, 1.3912436, 1.0702832, 3.7908, -0.52511805, 2.7853577, -0.2958057, 2.3954806, -0.2276556, -0.12555939, -0.08587316, -0.5877766, 0.045823403, 1.4249884, 3.011119, 1.0055817, 1.0201995]   

                                                                                                                                                                                                                                                                                                                                                                   subject_predictions                                                                                                                                                                                                                                                                                                                                                                   \
0  [4.3799605, 1.2472309, 0.59806883, 0.9923664, 0.99339515, 2.2244937, 0.74286425, 0.094959944, -0.9846684, -0.20609444, -0.07528155, 1.8362715, -0.6636215, -0.71567607, 1.2664436, 0.26790407, 1.2734845, 2.3071332, -0.34670073, -0.1275428, -0.512184, -0.34024775, -0.28231272, 0.31037122, -0.7364459, -0.38705784, 0.2520091, 1.4410205, 0.29374498, 0.7736282, 0.7041685, 3.7295218, 0.32358542, 3.8077881, 3.0731666, 0.18642747, 0.41756785, 0.5527588, 0.20870416, 0.059482135, 0.13233602, 0.5092442, 0.4813312, 2.2625208, -0.20975313, 1.5789889, 1.3912436, 1.0702832, 3.7908, -0.52511805, 2.7853577, -0.2958057, 2.3954806, -0.2276556, -0.12555939, -0.08587316, -0.5877766, 0.045823403, 1.4249884, 3.011119, 1.0055817, 1.0201995]   

                                                                                                                                                                                                                                                                                                                                                            object_predictions                                                                                                                                                                                                                                                                                                                                                           
0  [2.257394, -0.4615338, -0.25083154, -1.1822758, -1.1617206, 0.8028707, -0.25446495

In [93]:
"""
to get the features for the subject, select the dataframe sentences that aren't swapped and the prediction for the subject
"""
results = {}

subj = df[df['swapped?'] == False]
preds = subj.subject_predictions
average_subject_vector = np.average(preds, axis = 0)


subject_features = dict(zip(features,average_subject_vector))
results["original subject"] = subject_features

print()



In [94]:
"""
to get the features for the object, select the dataframe sentences that aren't swapped and the prediction for the object
"""

obj = df[df['swapped?'] == False]
preds = obj.object_predictions
average_object_vector = np.average(preds, axis = 0)

object_features = dict(zip(features,average_object_vector))
results["original object"] =  object_features


In [95]:
"""
to get the features for the (original) subject in swapped position, select the dataframe sentences that are swapped and the prediction for the object
"""
subj = df[df['swapped?'] == True]
preds = subj.object_predictions
average_swapped_subject_vector = np.average(preds, axis = 0)

swapped_subject_features = dict(zip(features,average_swapped_subject_vector))
results["swapped subject"] = swapped_subject_features


In [96]:
"""
to get the features for the (original) onject in swapped position, select the dataframe sentences that are swapped and the prediction for the subject
"""

subj = df[df['swapped?'] == True]
preds = subj.subject_predictions
average_swapped_object_vector = np.average(preds, axis = 0)

swapped_object_features = dict(zip(features,average_swapped_object_vector))
results["swapped object"] = swapped_object_features


In [134]:
df

id                                                      \
0                                                                                         reviews-211797-0020\n   
1                                                                                         reviews-211797-0020\n   
2                                                                                         reviews-211797-0007\n   
3                                                                                         reviews-211797-0007\n   
4                                                                                         reviews-053248-0002\n   
5                                                                                         reviews-053248-0002\n   
6                                                                                         reviews-363685-0030\n   
7                                                                                         reviews-363685-0030\n   
8                                                                                         reviews-363685-0010\n   
9                                                                                         reviews-363685-0010\n   
10                                                                                        reviews-290594-0006\n   
11                                                                                        reviews-290594-0006\n   
12                                                                                        reviews-290594-0005\n   
13                                                                                        reviews-290594-0005\n   
14                                                                                        reviews-026883-0010\n   
15                                                                                        reviews-026883-0010\n   
16                                                                                        reviews-036133-0009\n   
17                                                                                        reviews-036133-0009\n   
18                                                                                        reviews-018465-0012\n   
19                                                                                        reviews-018465-0012\n   
20                                                                                        reviews-018465-0011\n   
21                                                                                        reviews-018465-0011\n   
22                                                                                        reviews-220214-0004\n   
23                                                                                        reviews-220214-0004\n   
24                                                                                        reviews-269560-0009\n   
25                                                                                        reviews-269560-0009\n   
26                                                                                        reviews-018548-0014\n   
27                                                                                        reviews-018548-0014\n   
28                                                                                        reviews-216456-0004\n   
29                                                                                        reviews-216456-0004\n   
30                                                                                        reviews-326649-0007\n   
31                                                                                        reviews-326649-0007\n   
32                                                                                        reviews-210066-0006\n   
33                                                                                        reviews-210066-0006\n   
34                              

In [228]:

#print(results)
#pd.DataFrame.from_dict(results, orient='index')

graph = pd.DataFrame.from_records(results)

print(graph)



               original object  original subject  swapped object  \
Vision              2.570             3.446            2.613       
Bright              0.550             0.782            0.569       
Dark                0.438             0.772            0.515       
Color               0.679             1.306            0.828       
Pattern             0.755             1.064            0.802       
Large               1.413             1.780            1.303       
Small               0.823             0.718            0.767       
Motion              1.178             2.077            1.248       
Biomotion           1.033             2.665            1.536       
Fast                0.764             1.405            0.774       
Slow                0.423             0.843            0.560       
Shape               1.629             2.203            1.669       
Face                0.662             2.142            1.222       
Body                0.981             2.345     

In [229]:
graph = graph[['original subject', 'swapped subject', 'swapped object', 'original object']]
graph
#graph.columns.tolist()

original subject  swapped subject  swapped object  \
Vision               3.446            3.162            2.613       
Bright               0.782            0.649            0.569       
Dark                 0.772            0.607            0.515       
Color                1.306            1.096            0.828       
Pattern              1.064            0.966            0.802       
Large                1.780            1.615            1.303       
Small                0.718            0.841            0.767       
Motion               2.077            1.414            1.248       
Biomotion            2.665            1.767            1.536       
Fast                 1.405            0.810            0.774       
Slow                 0.843            0.593            0.560       
Shape                2.203            2.112            1.669       
Face                 2.142            1.556            1.222       
Body                 2.345            1.633            1.423       
Touch                0.838            0.947            0.872       
Temperature          0.781            0.698            0.526       
Texture              0.947            1.007            0.818       
Weight               1.550            1.560            1.229       
Pain                 0.702            0.633            0.602       
Audition             1.867            1.538            1.248       
Loud                 1.246            0.940            0.702       
Low                  0.502            0.398            0.274       
High                 0.583            0.485            0.346       
Sound                1.477            1.246            0.934       
Music                0.289            0.423            0.149       
Speech               2.144            1.652            1.360       
Taste                0.159            0.273            0.053       
Smell                0.526            0.561            0.306       
Head                 1.080            1.187            0.957       
UpperLimb            1.436            1.496            1.280       
LowerLimb            0.771            0.607            0.507       
Landmark             0.812            0.786            0.715       
Path                 1.157            0.636            0.772       
Scene                2.052            1.936            1.679       
Near                 0.858            0.982            1.049       
Toward               0.661            0.540            0.465       
Away                 0.723            0.529            0.601       
Number               0.622            0.876            0.785       
Time                 0.878            0.719            0.818       
Duration             1.067            0.855            1.045       
Long                 1.076            1.139            1.211       
Short                0.838            0.662            0.909       
Consequential        2.262            2.146            2.428       
Social               1.957            2.074            2.121       
Human                2.544            1.889            1.825       
Communication        1.314            1.459            1.582       
Self                 1.051            1.025            1.247       
Cognition            1.256            1.541            1.763       
Benefit              2.540            2.657            2.661       
Harm                 1.754            1.451            1.417       
Pleasant             1.982            2.065            1.879       
Unpleasant           1.064            0.988            1.024       
Happy                1.673            1.811            1.680       
Sad                  0.775            0.796            0.800       
Angry                0.768            0.728            0.761       
Disgusted            0.470            0.481            0.479       
Fearful              1.183            0.945            0.934       
Surprised            1.281            1.132            1.237       
Dri

In [230]:
%matplotlib
# Try to visualize this in a nice way 
import seaborn as sns; sns.set_theme()

#sns.heatmap(graph.reindex(graph.mean().sort_values().index, axis=1), cmap="coolwarm",annot=True)

ax = sns.heatmap(graph, cmap="coolwarm", yticklabels=True)

ax.plot()

Using matplotlib backend: MacOSX


[]

In [136]:
# just look at subject and object
ax = sns.heatmap(graph[['original subject', 'original object']], cmap="coolwarm", yticklabels=True)

ax.plot()

[]

In [141]:
#graph.index.name = 'Feature'
#graph.index.name

'Feature'

In [149]:
ax = sns.lineplot(x = 'Feature', y = 'original subject', ci=None, data=graph)
ax.plot()

[]

In [217]:
graph = graph.reset_index()
graph = graph.rename(columns={"index": 'Feature'})
graph

Feature      original subject  swapped subject  swapped object  \
0          Vision        3.446            3.162            2.613       
1          Bright        0.782            0.649            0.569       
2            Dark        0.772            0.607            0.515       
3           Color        1.306            1.096            0.828       
4         Pattern        1.064            0.966            0.802       
5           Large        1.780            1.615            1.303       
6           Small        0.718            0.841            0.767       
7          Motion        2.077            1.414            1.248       
8       Biomotion        2.665            1.767            1.536       
9            Fast        1.405            0.810            0.774       
10           Slow        0.843            0.593            0.560       
11          Shape        2.203            2.112            1.669       
12           Face        2.142            1.556            1.222       
13           Body        2.345            1.633            1.423       
14          Touch        0.838            0.947            0.872       
15    Temperature        0.781            0.698            0.526       
16        Texture        0.947            1.007            0.818       
17         Weight        1.550            1.560            1.229       
18           Pain        0.702            0.633            0.602       
19       Audition        1.867            1.538            1.248       
20           Loud        1.246            0.940            0.702       
21            Low        0.502            0.398            0.274       
22           High        0.583            0.485            0.346       
23          Sound        1.477            1.246            0.934       
24          Music        0.289            0.423            0.149       
25         Speech        2.144            1.652            1.360       
26          Taste        0.159            0.273            0.053       
27          Smell        0.526            0.561            0.306       
28           Head        1.080            1.187            0.957       
29      UpperLimb        1.436            1.496            1.280       
30      LowerLimb        0.771            0.607            0.507       
31       Landmark        0.812            0.786            0.715       
32           Path        1.157            0.636            0.772       
33          Scene        2.052            1.936            1.679       
34           Near        0.858            0.982            1.049       
35         Toward        0.661            0.540            0.465       
36           Away        0.723            0.529            0.601       
37         Number        0.622            0.876            0.785       
38           Time        0.878            0.719            0.818       
39       Duration        1.067            0.855            1.045       
40           Long        1.076            1.139            1.211       
41          Short        0.838            0.662            0.909       
42  Consequential        2.262            2.146            2.428       
43         Social        1.957            2.074            2.121       
44          Human        2.544            1.889            1.825       
45  Communication        1.314            1.459            1.582       
46           Self        1.051            1.025            1.247       
47      Cognition        1.256            1.541            1.763       
48        Benefit        2.540            2.657            2.661       
49           Harm        1.754            1.451            1.417       
50       Pleasant        1.982            2.065            1.879       
51     Unpleasant        1.064            0.988            1.024       
52          Happy        1.673            1.811            1.680       
53            Sad        0.775            0.796            0.800       
54          Angry        0.768            0.72

In [226]:
graph['Feature'] = graph['Feature'].astype(str)

graph['Feature'] = pd.Categorical(graph['Feature'], categories=map(str, graph.Feature), ordered=True)


df2 = pd.melt(graph, 'Feature', var_name='Grammatical Position', 
              value_name='Value')
df2 = df2.astype({'Value':'float'})
df2

Feature     Grammatical Position  Value
0           Vision   original subject    3.446
1           Bright   original subject    0.782
2             Dark   original subject    0.772
3            Color   original subject    1.306
4          Pattern   original subject    1.064
5            Large   original subject    1.780
6            Small   original subject    0.718
7           Motion   original subject    2.077
8        Biomotion   original subject    2.665
9             Fast   original subject    1.405
10            Slow   original subject    0.843
11           Shape   original subject    2.203
12            Face   original subject    2.142
13            Body   original subject    2.345
14           Touch   original subject    0.838
15     Temperature   original subject    0.781
16         Texture   original subject    0.947
17          Weight   original subject    1.550
18            Pain   original subject    0.702
19        Audition   original subject    1.867
20            Loud   original subject    1.246
21             Low   original subject    0.502
22            High   original subject    0.583
23           Sound   original subject    1.477
24           Music   original subject    0.289
25          Speech   original subject    2.144
26           Taste   original subject    0.159
27           Smell   original subject    0.526
28            Head   original subject    1.080
29       UpperLimb   original subject    1.436
30       LowerLimb   original subject    0.771
31        Landmark   original subject    0.812
32            Path   original subject    1.157
33           Scene   original subject    2.052
34            Near   original subject    0.858
35          Toward   original subject    0.661
36            Away   original subject    0.723
37          Number   original subject    0.622
38            Time   original subject    0.878
39        Duration   original subject    1.067
40            Long   original subject    1.076
41           Short   original subject    0.838
42   Consequential   original subject    2.262
43          Social   original subject    1.957
44           Human   original subject    2.544
45   Communication   original subject    1.314
46            Self   original subject    1.051
47       Cognition   original subject    1.256
48         Benefit   original subject    2.540
49            Harm   original subject    1.754
50        Pleasant   original subject    1.982
51      Unpleasant   original subject    1.064
52           Happy   original subject    1.673
53             Sad   original subject    0.775
54           Angry   original subject    0.768
55       Disgusted   original subject    0.470
56         Fearful   original subject    1.183
57       Surprised   original subject    1.281
58           Drive   original subject    1.841
59           Needs   original subject    1.511
60       Attention   original subject    2.707
61         Arousal   original subject    2.238
62          Vision    swapped subject    3.162
63          Bright    swapped subject    0.649
64            Dark    swapped subject    0.607
65           Color    swapped subject    1.096
66         Pattern    swapped subject    0.966
67           Large    swapped subject    1.615
68           Small    swapped subject    0.841
69          Motion    swapped subject    1.414
70       Biomotion    swapped subject    1.767
71            Fast    swapped subject    0.810
72            Slow    swapped subject    0.593
73           Shape    swapped subject    2.112
74            Face    swapped subject    1.556
75            Body    swapped subject    1.633
76           Touch    swapped subject    0.947
77     Temperature    swapped subject    0.698
78         Texture    swapped subject    1.007
79          Weight    swapped subject    1.560
80            Pain    swapped subject    0.633
81        Audition    swapped subject    1.538
82            Loud    swapped subject    0.940
83             Low    swapped subject    0.398
84          

In [222]:
# try to make a pretty line chart


sns.lineplot('Feature', 'Value', hue='Grammatical Position', data=df2)

ConversionError: Failed to convert value(s) to axis units: array([], dtype=float64)

### This is the Delta Analysis

In [50]:
print(df.id.unique())

['reviews-211797-0020\n' 'reviews-211797-0007\n' 'reviews-053248-0002\n'
 'reviews-363685-0030\n' 'reviews-363685-0010\n' 'reviews-290594-0006\n'
 'reviews-290594-0005\n' 'reviews-026883-0010\n' 'reviews-036133-0009\n'
 'reviews-018465-0012\n' 'reviews-018465-0011\n' 'reviews-220214-0004\n'
 'reviews-269560-0009\n' 'reviews-018548-0014\n' 'reviews-216456-0004\n'
 'reviews-326649-0007\n' 'reviews-210066-0006\n' 'reviews-183518-0012\n'
 'reviews-183518-0006\n' 'reviews-183518-0003\n' 'reviews-292841-0003\n'
 'reviews-225632-0009\n' 'reviews-018562-0004\n' 'reviews-018562-0002\n'
 'reviews-091704-0004\n' 'reviews-085980-0005\n' 'reviews-349020-0011\n'
 'reviews-349020-0002\n' 'reviews-310032-0010\n' 'reviews-234261-0004\n'
 'reviews-121342-0003\n' 'reviews-011257-0002\n' 'reviews-365154-0002\n'
 'reviews-165143-0005\n' 'reviews-194316-0005\n' 'reviews-055976-0005\n'
 'reviews-055976-0001\n' 'reviews-292997-0006\n' 'reviews-292997-0005\n'
 'reviews-122882-0002\n' 'reviews-280340-0001\n' 'r

In [89]:
len(eval_words)

57

In [ ]:
# subject analysis""""""

In [57]:
deltas = []

for idd in df.id.unique():
    preds = df[df['id'] == idd]
    subj = preds[preds['swapped?'] == False]
    obj = preds[preds['swapped?'] == True]

    subj_avg = np.average(subj.predictions)
    obj_avg = np.average(obj.predictions)
    delta = subj_avg - obj_avg
    deltas.append(delta)
    
    #print(idd)
    #print(dict(zip(features,delta)))
    
print("average delta from subj to swapped subject across lemmas")
avg_delta = np.average(deltas, axis = 0)
print(dict(zip(features,avg_delta)))


average delta from literal to metaphorical across lemmas
{'Vision': 0.8246117, 'Bright': 0.21456069, 'Dark': 0.2526856, 'Color': 0.47668418, 'Pattern': 0.26322135, 'Large': 0.47054046, 'Small': -0.043338876, 'Motion': 0.8220606, 'Biomotion': 1.1180984, 'Fast': 0.62697107, 'Slow': 0.28306654, 'Shape': 0.53242135, 'Face': 0.90685654, 'Body': 0.9082711, 'Touch': -0.028793285, 'Temperature': 0.2550151, 'Texture': 0.13436139, 'Weight': 0.32473743, 'Pain': 0.090332896, 'Audition': 0.6127391, 'Loud': 0.5357486, 'Low': 0.22546405, 'High': 0.2349806, 'Sound': 0.53760874, 'Music': 0.1383289, 'Speech': 0.7731486, 'Taste': 0.10726186, 'Smell': 0.22169325, 'Head': 0.12662771, 'UpperLimb': 0.15805228, 'LowerLimb': 0.2591113, 'Landmark': 0.096863665, 'Path': 0.3845242, 'Scene': 0.37370035, 'Near': -0.18596387, 'Toward': 0.1970167, 'Away': 0.12259061, 'Number': -0.16172442, 'Time': 0.064563096, 'Duration': 0.024912912, 'Long': -0.13473247, 'Short': -0.06747472, 'Consequential': -0.1662817, 'Social': -

In [55]:
# so we want to take each category
coarse_categories = set(feature_categories.values())

In [56]:
results = dict()
for coarse_cat in coarse_categories:
    print(coarse_cat)
    delta_results = []
    for delta in deltas:

        delta = dict(zip(features,delta))
        #print(delta)

        res = []
        for key, value in delta.items():
            if feature_categories[key] == coarse_cat:
                #print(coarse_cat)
                #print(value)
                res.append(value)
        #print(len(res))
        #print(res)
        res = np.average(res)
        #print(res)
        delta_results.append(res)
    results[coarse_cat] = np.average(delta_results)
print(results)

Gustation
Olfaction
Attention
Motor
Temporal
Causal
Somatic
Emotion
Cognition
Audition
Social
Spatial
Vision
Drive
{'Gustation': 0.10726185, 'Olfaction': 0.22169326, 'Attention': 0.27309164, 'Motor': 0.18126373, 'Temporal': -0.028182797, 'Causal': -0.16628167, 'Somatic': 0.15513071, 'Emotion': 0.060130585, 'Cognition': -0.49800748, 'Audition': 0.4368598, 'Social': 0.027550861, 'Spatial': 0.11814391, 'Vision': 0.5469079, 'Drive': -0.19901825}


# construction analysis

hypothesis: nouns in ASNs (argument supporting constructions) will behave more like metaphorical language in emphasizing abstract features. and nouns in compounds will behave more liek literal uses, with emphasis of physical features

In [91]:
# check that we've got this label coded correctly
eval_words.normalized_construction.unique()

array(['modifier_x', 'prep_complement', 'compound', 'verb'], dtype=object)

In [98]:
const_deltas = []

for lemma in eval_words.lemma.unique():
    preds = eval_words[eval_words['word'] == lemma]
    lit = preds[preds['normalized_construction'] == 'compound']
    met = preds[preds['normalized_construction'] == 'prep_complement']

    lit_avg = np.average(met.predictions)
    met_avg = np.average(lit.predictions)
    delta = lit_avg - met_avg
    const_deltas.append(delta)
    
    print(lemma)
    print(dict(zip(features,delta)))
    
print("average delta from compound (lit) to prep complement (met) across lemmas")
avg_delta = np.average(deltas, axis = 0)
print(dict(zip(features,avg)))

collapse
{'Vision': -0.49171996, 'Bright': -0.3067559, 'Dark': -0.42609853, 'Color': -0.7228577, 'Pattern': -0.5045803, 'Large': -0.71385074, 'Small': 0.09049165, 'Motion': -0.31519198, 'Biomotion': 0.27527595, 'Fast': -0.26784182, 'Slow': -0.22224322, 'Shape': -0.58232665, 'Face': 0.52744395, 'Body': 0.5994586, 'Touch': 0.031878203, 'Temperature': -0.4736963, 'Texture': -0.2786922, 'Weight': -0.51478946, 'Pain': -0.35493445, 'Audition': 0.312212, 'Loud': -0.015454292, 'Low': 0.01142323, 'High': 0.19196993, 'Sound': 0.06910312, 'Music': 0.3025833, 'Speech': 0.6156839, 'Taste': -0.09012462, 'Smell': -0.3605376, 'Head': 0.45471847, 'UpperLimb': 0.707011, 'LowerLimb': -0.0066573024, 'Landmark': -0.38008493, 'Path': -0.25892484, 'Scene': -0.42575854, 'Near': 0.17477798, 'Toward': -0.055330873, 'Away': -0.044544935, 'Number': -0.1135366, 'Time': -0.11053038, 'Duration': -0.096343994, 'Long': -0.21440649, 'Short': 0.1968143, 'Consequential': -0.0645628, 'Social': 0.46081984, 'Human': 0.86238

In [100]:
results = dict()
for coarse_cat in coarse_categories:
    print(coarse_cat)
    delta_results = []
    for delta in const_deltas:

        delta = dict(zip(features,delta))
        #print(delta)

        res = []
        for key, value in delta.items():
            if feature_categories[key] == coarse_cat:
                #print(coarse_cat)
                #print(value)
                res.append(value)
        #print(len(res))
        #print(res)
        res = np.average(res)
        print(res)
        delta_results.append(res)
    results[coarse_cat] = np.average(delta_results)
#print(results)

Causal
-0.0645628
-0.38981843
-0.16397333
Vision
-0.21862833
0.12004639
0.31502256
Social
0.5642164
-0.1222862
0.28738648
Cognition
0.5416862
0.015124083
0.17980576
Emotion
-0.12432009
-0.27671796
-0.08532443
Drive
0.20570996
0.28784436
-0.07900095
Attention
-0.102904916
-0.6068026
0.060249925
Spatial
-0.15762897
0.010953302
0.103421904
Audition
0.21250303
-0.4132634
0.12924932
Gustation
-0.09012462
0.06645012
-0.2676504
Somatic
-0.31804684
-0.022410352
-0.107581474
Temporal
-0.05611664
-0.28529233
-0.075606644
Motor
0.38502407
-0.22612226
0.071339406
Olfaction
-0.3605376
-0.07619703
-0.48292324
